In [1]:
# Generic
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import warnings, gc
warnings.filterwarnings("ignore")

# Tensorflow
import tensorflow as tf

# ktrain
import ktrain
from ktrain import text

# sklearn
from sklearn.model_selection import train_test_split


In [2]:
df = pd.read_csv("TrainingDataForBERTMODEL-VisualAid-Binary.csv", header='infer')
# Dropping Null Values
df.dropna(inplace=True)

# Total Records
print("Total Records: ", df.shape[0])

# Inspect
df.head()


Total Records:  2038


Topic                                   Sentence
0    No     Begins with a story to engage audience
1    No  He clasps his hands a lot while he speaks
2    No                              Use of humour
3    No                             Use of analogy
4    No                  He makes good eye contact

In [3]:
# Data Split
target = ['Topic']
data = ['Sentence']

X = df[data]
y = df[target]

X_train, X_test, y_train, y_test = train_test_split(X, y , test_size=0.1, random_state=42)

In [4]:
# Common Parameters
max_len = 500
batch_size = 16
learning_rate = 5e-5
epochs = 5

In [5]:
#########
## With Transformer = bert-base-uncased
######
# Transformer Model
model_ = 'bert-base-uncased'
t_mod = text.Transformer(model_, maxlen=500, classes = [0,1])


'''Converting split data to list [so it can processed]'''
#train
X_tr = X_train['Sentence'].tolist()
y_tr = y_train['Topic'].tolist()

#test
X_ts = X_test['Sentence'].tolist()
y_ts = y_test['Topic'].tolist()


# Pre-processing training & test data
train = t_mod.preprocess_train(X_tr,y_tr)
test = t_mod.preprocess_train(X_ts,y_ts)

# Model Classifier
model = t_mod.get_classifier()

learner = ktrain.get_learner(model, train_data=train, val_data=test, batch_size=batch_size)

preprocessing train...
language: en
train sequence lengths:
	mean : 11
	95percentile : 28
	99percentile : 52


Is Multi-Label? False
preprocessing train...
language: en
train sequence lengths:
	mean : 12
	95percentile : 25
	99percentile : 54


Is Multi-Label? False


In [6]:
# Train Model
learner.fit_onecycle(learning_rate, epochs)



begin training using onecycle policy with max lr of 5e-05...
Epoch 1/5
115/115 [==============================] - 8947s 78s/step - loss: 0.4523 - accuracy: 0.8097 - val_loss: 0.1996 - val_accuracy: 0.9461
Epoch 2/5
115/115 [==============================] - 8555s 74s/step - loss: 0.1922 - accuracy: 0.9329 - val_loss: 0.1881 - val_accuracy: 0.9461
Epoch 3/5
115/115 [==============================] - 10224s 89s/step - loss: 0.1036 - accuracy: 0.9673 - val_loss: 0.1913 - val_accuracy: 0.9412
Epoch 4/5
115/115 [==============================] - 8645s 75s/step - loss: 0.0520 - accuracy: 0.9831 - val_loss: 0.1961 - val_accuracy: 0.9559
Epoch 5/5
115/115 [==============================] - 8679s 75s/step - loss: 0.0219 - accuracy: 0.9940 - val_loss: 0.1673 - val_accuracy: 0.9657


In [64]:
# Evaluate
x = learner.validate(class_names=t_mod.get_classes())

              precision    recall  f1-score   support

          No       0.96      0.99      0.98       158
 Visual Aids       0.98      0.87      0.92        46

    accuracy                           0.97       204
   macro avg       0.97      0.93      0.95       204
weighted avg       0.97      0.97      0.96       204



In [68]:
predictor = ktrain.get_predictor(learner.model, preproc=t_mod)
predictor.save('VisualaidBinaryClassifier')
print('Model Saved')

Model Saved


In [9]:
model.save('completeVisual_saved_model/')

In [ ]:
df1=pd.read_csv("PresentationSkillDataSetForBert.csv")
#classes = ['Delivery','Structure','Visual Aids']
classes = ['VisualAid','']
predictor = ktrain.get_predictor(learner.model, preproc=t_mod)

segmentId=df1['SegmentId']
segList=list(segmentId)

startTime=df1['StartTime']
strList=list(startTime)

endTime=df1['EndTime']
endList=list(endTime)

transcript=df1['Transcript']
transList=list(transcript)
transList1=[]
for i in transList:
    if i != 'nan':
        transList1.append(i)
for i in transList1:
    print(i)
    print()

In [ ]:
#predictor.save('DeliveryBinaryClassifier')
ktrain.get_predictor(learner.model, preproc=t_mod).save('VisualAidBinaryClassifier')


In [ ]:
learner.model.save_pretrained('VisualAidBinaryClassifier')

In [134]:
i=0
segTranscript=[]
allSegmentsTrans=[]
startime=strList[0]
endTime=endList[0]
segTrigger=i
while i < len(segList)-2:
    #print(segList[i])
    #print()
    if segList[i]==segList[i+1]:
        print(segList[i],'  ==  ',segList[i+1])
        print()
        segTranscript.append(transList1[i])
        #segTranscript.append(transList1[i+1])
        print( transList1[i])
        #print( transList1[i+1])
        print()
        i+=1
    else:
        print(segList[i],'  !=  ',segList[i+1])
        #print()
        #print('start time= ',strList[i+1],'    ','end time= ',endList[i+1])

        segTranscript.append(transList1[i])
        listToString=' '.join([str(item) for item in segTranscript ])
        allSegmentsTrans.append([segList[i],startime,endTime,segTranscript,listToString])
        print(listToString)
        print()
        segTranscript=[]
        
        startime=strList[i+1]
        endTime=endList[i+1]
        
        i+=1

TmbQFWBvTtY1   ==   TmbQFWBvTtY1

  When we stand and present we want to come across a confident and composed .

TmbQFWBvTtY1   ==   TmbQFWBvTtY1

  And one of the great way to do that is by working on our body language . Let 's

TmbQFWBvTtY1   ==   TmbQFWBvTtY1

  look at three way to improve your nonverbal body language in presentation .

TmbQFWBvTtY1   ==   TmbQFWBvTtY1

  Coming up .

TmbQFWBvTtY1   ==   TmbQFWBvTtY1

  Hello again friend . If you never seen one of my video I 'm Alex Lyon .

TmbQFWBvTtY1   !=   TmbQFWBvTtY2
  When we stand and present we want to come across a confident and composed .   And one of the great way to do that is by working on our body language . Let 's   look at three way to improve your nonverbal body language in presentation .   Coming up .   Hello again friend . If you never seen one of my video I 'm Alex Lyon .   And this channel Communication Coach is here to help you increase

TmbQFWBvTtY2   ==   TmbQFWBvTtY2

  your impact so you can lead your te


MnIPpUiTcRc28   ==   MnIPpUiTcRc28

  audience because because if you 're not

MnIPpUiTcRc28   ==   MnIPpUiTcRc28

  they will know and you will have lost

MnIPpUiTcRc28   ==   MnIPpUiTcRc28

  all credibility tip number six be

MnIPpUiTcRc28   ==   MnIPpUiTcRc28

  relatable being relatable is actually

MnIPpUiTcRc28   !=   MnIPpUiTcRc29
  to be true always be honest with your   audience because because if you 're not   they will know and you will have lost   all credibility tip number six be   relatable being relatable is actually   one of the most important factor of

MnIPpUiTcRc29   ==   MnIPpUiTcRc29

  your delivery you want to be someone

MnIPpUiTcRc29   ==   MnIPpUiTcRc29

  that your audience can relate to but

MnIPpUiTcRc29   ==   MnIPpUiTcRc29

  they would feel comfortable with talking

MnIPpUiTcRc29   ==   MnIPpUiTcRc29

  to even when giving a talk a an expert

MnIPpUiTcRc29   ==   MnIPpUiTcRc29

  on a topic you want the audience to feel

MnIPpUiTcRc29   !=   MnIPpUiTcR

  when you 're having the slide up for a short period of time . Do n't make it like a photo   album . Do n't put million and seven picture and ... Keep it simple . Put a single image   on each slide . Try and pick image that you actually like and not too distracting . You   do n't want puppy dog and thing . Make something simple but something that you like and make   sure it look nice .   The next one you have to worry about is the lettering . So the lettering you also might

eHhqWbI0y4M5   ==   eHhqWbI0y4M5

  know this a the font . So font and lettering are the same . One thing that you do not want

eHhqWbI0y4M5   ==   eHhqWbI0y4M5

  to do is have really fancy or beautiful lettering . Simply ... The reason is some people ca n't

eHhqWbI0y4M5   ==   eHhqWbI0y4M5

  read when the letter are fancy especially if you are doing presentation for people

eHhqWbI0y4M5   ==   eHhqWbI0y4M5

  whose ... Do not have English a their first language if you take the letter and you

eHhqWbI0y4M5   ==

  IPO firm tend to underperform for the first two year .   These finding are also supported by more recent research .   In a 2019 paper from Dimensional Fund Advisors   the author examined 6   between January 1991 and December 2018 .   To evaluate IPO performance a a whole

oSZfqCBUpOs24   ==   oSZfqCBUpOs24

  they constructed a hypothetical

oSZfqCBUpOs24   ==   oSZfqCBUpOs24

  market weighted portfolio of IPOs

oSZfqCBUpOs24   ==   oSZfqCBUpOs24

  issued over the preceding 12 period

oSZfqCBUpOs24   ==   oSZfqCBUpOs24

  and rebalanced monthly .

oSZfqCBUpOs24   ==   oSZfqCBUpOs24

  They excluded first return from the analysis .

oSZfqCBUpOs24   !=   oSZfqCBUpOs25
  they constructed a hypothetical   market weighted portfolio of IPOs   issued over the preceding 12 period   and rebalanced monthly .   They excluded first return from the analysis .   They found that over the full sample period

oSZfqCBUpOs25   ==   oSZfqCBUpOs25

  the IPO portfolio delivered a return of 6.93 %

oSZf

Js7-OWd19PE56   ==   Js7-OWd19PE56

 we have something already with us that

Js7-OWd19PE56   ==   Js7-OWd19PE56

 we carry with us every day which is our

Js7-OWd19PE56   ==   Js7-OWd19PE56

 physical presence and I want to take

Js7-OWd19PE56   ==   Js7-OWd19PE56

 that last word presence because it's so

Js7-OWd19PE56   ==   Js7-OWd19PE56

 important there are five dimensions of

Js7-OWd19PE56   !=   Js7-OWd19PE57
 we have something already with us that  we carry with us every day which is our  physical presence and I want to take  that last word presence because it's so  important there are five dimensions of  presence that we need in a presentation

Js7-OWd19PE57   ==   Js7-OWd19PE57

 or a pitch basically a pitch is a

Js7-OWd19PE57   ==   Js7-OWd19PE57

 presentation of an idea right it's

Js7-OWd19PE57   ==   Js7-OWd19PE57

 trying to hook someone in one is that

Js7-OWd19PE57   ==   Js7-OWd19PE57

 you if you're making this presentation

Js7-OWd19PE57   ==   Js7-OWd19PE57

 hav

...

  we will not be living in familiar   situation   often you are going to encounter   unfamiliar situation   develop the habit of speaking if you do   not have confidence

P4zxWqC_fCY58   ==   P4zxWqC_fCY58

  build up the level of confidence why are

P4zxWqC_fCY58   ==   P4zxWqC_fCY58

  you worried what others are going to

P4zxWqC_fCY58   ==   P4zxWqC_fCY58

  think about you

P4zxWqC_fCY58   ==   P4zxWqC_fCY58

  you should be worried about yourself you

P4zxWqC_fCY58   ==   P4zxWqC_fCY58

  should be thinking always about yourself

P4zxWqC_fCY58   !=   P4zxWqC_fCY59
  build up the level of confidence why are   you worried what others are going to   think about you   you should be worried about yourself you   should be thinking always about yourself   if you 're thinking more about others and

P4zxWqC_fCY59   ==   P4zxWqC_fCY59

  le about yourself

P4zxWqC_fCY59   ==   P4zxWqC_fCY59

  that mean you are doing injustice with

P4zxWqC_fCY59   ==   P4zxWqC_fCY59

  yourself so therefo

P4zxWqC_fCY173   ==   P4zxWqC_fCY173

  work out on your volume work out on the

P4zxWqC_fCY173   ==   P4zxWqC_fCY173

  tone

P4zxWqC_fCY173   !=   P4zxWqC_fCY174
  language of the audience   so when you are working on these again i   say   work out on your volume work out on the   tone   and work out on the face do n't be a very

P4zxWqC_fCY174   ==   P4zxWqC_fCY174

  fast reader or speaker

P4zxWqC_fCY174   ==   P4zxWqC_fCY174

  you should always work out on uh the

P4zxWqC_fCY174   ==   P4zxWqC_fCY174

  pace at which you 're going to

P4zxWqC_fCY174   ==   P4zxWqC_fCY174

  communicate with others the volume

P4zxWqC_fCY174   ==   P4zxWqC_fCY174

  matter a lot

P4zxWqC_fCY174   !=   P4zxWqC_fCY175
  fast reader or speaker   you should always work out on uh the   pace at which you 're going to   communicate with others the volume   matter a lot   along with the tonality of the voice

P4zxWqC_fCY175   ==   P4zxWqC_fCY175

  okay

P4zxWqC_fCY175   ==   P4zxWqC_fCY175

  when you d

  moved to something else so do not confuse them and they will ah feel

JF_m8AhkxuM18   ==   JF_m8AhkxuM18

  the monotony do not leave visual slide too long so even if you can not change it dont

JF_m8AhkxuM18   !=   JF_m8AhkxuM19
  it for a long time because it loses it 's relevant and audience will also lose interest in your   talk because they will just look at the visual and they will feel that you are just still   continuing with the same ah thought in term of visuals but in term of verbal you have   moved to something else so do not confuse them and they will ah feel   the monotony do not leave visual slide too long so even if you can not change it dont   just leave it so close it keep it away and then continue with your talk so the audience

JF_m8AhkxuM19   ==   JF_m8AhkxuM19

  attention is focus towards your speech not on the visual and if you are going to use

JF_m8AhkxuM19   ==   JF_m8AhkxuM19

  power point they or any kind of visual to move one after another who will do t

rvIfl5Q66T036   !=   rvIfl5Q66T037
  hopefully you will be able to deliver   your presentation without saying so here   i will show you this thing i 'm not going   to show you which would be really good   will help you but i am from it that 's   not very helpful so try to have it let

rvIfl5Q66T037   ==   rvIfl5Q66T037

  me and this also might give everything

rvIfl5Q66T037   ==   rvIfl5Q66T037

  for you

rvIfl5Q66T037   ==   rvIfl5Q66T037

  team with your attention if you know

rvIfl5Q66T037   ==   rvIfl5Q66T037

  that word stop store you still prepared

rvIfl5Q66T037   ==   rvIfl5Q66T037

  that is a very good another little

rvIfl5Q66T037   !=   rvIfl5Q66T038
  me and this also might give everything   for you   team with your attention if you know   that word stop store you still prepared   that is a very good another little   technique to make yourself feel le

rvIfl5Q66T038   ==   rvIfl5Q66T038

  anxious because if you know that you 're

rvIfl5Q66T038   ==   rvIfl5Q66T038

  

rvIfl5Q66T0153   ==   rvIfl5Q66T0153

  at the same time it 's inclusive but i

rvIfl5Q66T0153   ==   rvIfl5Q66T0153

  think if i look at what you 've told u

rvIfl5Q66T0153   ==   rvIfl5Q66T0153

  to any that if these people with thing

rvIfl5Q66T0153   !=   rvIfl5Q66T0154
  that they put a bunch of stuff up so I   ca n't concentrate a live in PowerPoint   at the same time it 's inclusive but i   think if i look at what you 've told u   to any that if these people with thing   all this wishy washy snuggle I know what

rvIfl5Q66T0154   ==   rvIfl5Q66T0154

  to do this should make it clear ca n't

rvIfl5Q66T0154   ==   rvIfl5Q66T0154

  lie down if the audience doe n't because

rvIfl5Q66T0154   ==   rvIfl5Q66T0154

  if that 's what happens when you talk

rvIfl5Q66T0154   ==   rvIfl5Q66T0154

  about the situation when people put pop

rvIfl5Q66T0154   ==   rvIfl5Q66T0154

  up hard when they talk about something

rvIfl5Q66T0154   !=   rvIfl5Q66T0155
  to do this should make it clear 

In [135]:
for i in allSegmentsTrans:
    print(i)
    print()

['TmbQFWBvTtY1', 0.0, 0.22, ['  When we stand and present we want to come across a confident and composed .', "  And one of the great way to do that is by working on our body language . Let 's", '  look at three way to improve your nonverbal body language in presentation .', '  Coming up .', "  Hello again friend . If you never seen one of my video I 'm Alex Lyon .", '  And this channel Communication Coach is here to help you increase'], "  When we stand and present we want to come across a confident and composed .   And one of the great way to do that is by working on our body language . Let 's   look at three way to improve your nonverbal body language in presentation .   Coming up .   Hello again friend . If you never seen one of my video I 'm Alex Lyon .   And this channel Communication Coach is here to help you increase"]

['TmbQFWBvTtY2', 0.25, 0.43, ['  your impact so you can lead your team to higher level of excellence . And I', '  believe that presentation skill are a really i

['kw_udjD2xwo6', 2.19, 2.41, ['  shine .', "  It 's also important to note that not every object need an animation .", '  This is especially true in more corporate or professional setting .', "  In this case we 're creating a fairly casual presentation—so I 'm going to add one more", '  effect to our little astronaut but leave the rest of the slide alone .', '  At this point we have several animation to keep track of so it might be a good time'], "  shine .   It 's also important to note that not every object need an animation .   This is especially true in more corporate or professional setting .   In this case we 're creating a fairly casual presentation—so I 'm going to add one more   effect to our little astronaut but leave the rest of the slide alone .   At this point we have several animation to keep track of so it might be a good time"]

['kw_udjD2xwo7', 2.48, 3.07, ['  to open the Animation Pane .', '  The pane appears on the right and let you do a few different thing .', '  Yo

In [136]:
#### 
# Write the annotation result to Excel File

import xlrd
import xlsxwriter
workbook = xlsxwriter.Workbook('PresentationCorpusAnnotatedUsingBertBaseUncase-BinaryDelivery.xlsx')
worksheet = workbook.add_worksheet('Sheet1')
worksheet.write('A1', 'SegmentId')
worksheet.write('B1', 'StartTime')
worksheet.write('C1', 'EndTime')
worksheet.write('D1', 'Transcript')
worksheet.write('E1', 'Topic')
row=1
col=0
transRow=0

for i in allSegmentsTrans:
    print(i[0])
    print(i[4])
    print()
    print('row= ',row)
    print()
    mainRow=row
    worksheet.write(row,col,i[0])
    worksheet.write(row,col+1,i[1])
    worksheet.write(row,col+2,i[2])
    transRow=row
    for j in i[3]:
        worksheet.write(row,col+3,j)
        row+=1
    print('prediction= ',predictor.predict(i[4]))
    print()
    worksheet.write(mainRow,col+4,predictor.predict(i[4]))
        
        

    
workbook.close()        

#pred_class = predictor.predict(transList )
#print("Predicted Class: ", predictor.predict(transList ))


TmbQFWBvTtY1
  When we stand and present we want to come across a confident and composed .   And one of the great way to do that is by working on our body language . Let 's   look at three way to improve your nonverbal body language in presentation .   Coming up .   Hello again friend . If you never seen one of my video I 'm Alex Lyon .   And this channel Communication Coach is here to help you increase

row=  1

prediction=  No

TmbQFWBvTtY2
  your impact so you can lead your team to higher level of excellence . And I   believe that presentation skill are a really important part of leadership .   You 're going to be standing and presenting quite frequently if you 're in   any kind of leadership position . So we want to get just a little bit better at   this . Let 's look at three way you can improve your nonverbal body language so   that people can hear your message in a much more confident and composed way .

row=  7

prediction=  No

TmbQFWBvTtY3
  And these tip by the way go togeth

prediction=  No

1VCaJ4dSHak6
  So we can use these gesture to symbolise the feeling that we have and that also emphatic   gesture help u in more genuine â€˜so what are you talking about I am so angry when   this happened and we are using this angry gesture it actually give more humph to our   presentation and make sing more genuine yes he were angry I can see his body language   he wa angryâ€™ but if you were saying â€˜Yeah I wa really angryâ€™ and your body language   is just slumped and you kind of look depressed well may be they are not going to believe

row=  103

prediction=  No

1VCaJ4dSHak7
  that you are actually angry .   So actually it give make your presentation look more genuine .   Number three a Suggestive gesture so these are the thing like mood an expression   for example : you could say I welcome you in with open arm since you got your open palm   symbolises that you are open .   So you could say that this guy in audience who wa just wonâ€™t listen to anything else

r

prediction=  Visual Aids

dEDcc0aCjaA15
  like this .   The purpose of this step is to show your audience the takeaway for your presentation  the   thing they get to `` take away '' and use tomorrow after listening to your presentation .   Do n't read the slide .   They 're adult .   They can read .

row=  380

prediction=  Visual Aids

dEDcc0aCjaA16
  Instead just give them a moment to read it themselves and introduce your agenda by summarizing   what you 'll be doing .   You do this by mentioning the number of takeaway you 'll be giving them and paraphrasing the   goal of your presentation .   Here 's what it look like :   `` I 'm going to show you 5 step to deliver a killer opener . ''

row=  386

prediction=  No

dEDcc0aCjaA17
  What would this look like for you ?   The last step is Step 5 Give a Credible Statement .   You can do this by giving relevant or compelling data to your audience to support your message .   Remember how I did this at the beginning of this video ?   I said 

MnIPpUiTcRc19
  repetition this encourages people to   remember the key point of the   presentation and help it stick which   again make it and you more memorable a   classic way to go about repetition is   something Dana learned early on when he

row=  539

prediction=  No

MnIPpUiTcRc20
  started his public speaking career   another speaker at a big regional tech   event came up to him after a talk and   complimented Dana on is delivery in the   depth of the material but asked why he   did n't use more repetition Dana wa a

row=  545

prediction=  No

MnIPpUiTcRc21
  bit stumped because he never really   thought about that before the other   speaker suggested that Dana start   telling the audience what it is he   wanted to tell them just to give them a   brief rundown of the key point after

row=  551

prediction=  No

MnIPpUiTcRc22
  that move right into the body of the   presentation and tell them exactly what   wa highlighted at the beginning but   obviously with more detail and e

prediction=  No

gaoxXFju6uo6
  and finally how do you say goodbye right ?   That make sense to me .   If you 're giving a pitch and you 're at a meeting right ?   And you 're trying to figure out how to structure thing maybe you think about it from the   customer 's perspective .   First they 're gon na hit the marketing team then they 're gon na finally meet the sale team .

row=  704

prediction=  No

gaoxXFju6uo7
  And once they get sold they 're gon na go to the deliverable team .   Whatever it is the piece should flow naturally in your head .   That will save you so much memorization work down the line that 's why I avoid memorizing .   The second piece is that once you have these bullet you flush them out .   I will actually go in and I type everything that I can think of underneath each bullet .   That includes story thing that I want to get detail that I might not have thought of .

row=  710

prediction=  No

gaoxXFju6uo8
  That 's gon na help me communicate my main point .  

...

F977vuuxAGA117
  this purple item and then select a   different color   like that so you know if you 've used   powerpoint you use microsoft word   the dashboard up here is fairly easy to   use

row=  9812

prediction=  Visual Aids

F977vuuxAGA118
  but you 'll notice that it change   depending on the element   that you choose so if you choose an   image it 'll tell you   replace an image if you choose you know   a color block it 'll tell you there 's

row=  9818

prediction=  Visual Aids

F977vuuxAGA119
  different option for the color block   if you choose text on the other hand you   have the opportunity to   you know change the size increase it   change the font   type you can bold italicize background

row=  9824

prediction=  Visual Aids

F977vuuxAGA120
  color   the color alignment so really basic   stuff when it come to   text stuff that you would see in a   pretty much most word processing system   now let 's say you want to add something

row=  9830

prediction=  Visual Aids


F977vuuxAGA152
  going to be different   with mac computer it might be command   a but what i just did wa i selected   everything all the topic so control   a is select all and that 's pretty   standard with

row=  10022

prediction=  No

F977vuuxAGA153
  most word processing or even browser   function is   ctrl a selects all by selecting all that   enables you to move thing around   a little bit better so instead of moving   item like little

row=  10028

prediction=  Visual Aids

F977vuuxAGA154
  topic one by one by one you can   literally select   everything and move it around so you can   select and move   here and move it here now   i could select all and i can also copy

row=  10034

prediction=  No

F977vuuxAGA155
  by clicking control   c or command key and control v   which will basically copy everything   now i do n't see where you would actually   need to do that   unless you had a lot of these item

row=  10040

prediction=  Visual Aids

F977vuuxAGA156
  right   so if we we

F977vuuxAGA187
  but   that said you will need to have   camtasia or screenflow so in order to do   this   you will need obviously to dish out   either 150 to 300

row=  10232

prediction=  No

F977vuuxAGA188
  to get access to these software you   will also need to have   a microphone either a usb microphone or   a more professional microphone   i believe with mac computer you can   easily use

row=  10238

prediction=  Visual Aids

F977vuuxAGA189
  the the microphone earbuds you can use   those a well   to record a video but all you do is just   go into presentation mode   now that you have an idea of prezi   classic versus prezi next

row=  10244

prediction=  Visual Aids

F977vuuxAGA190
  all you have to do is click present   now you 'll notice that if i put my mouse   down here this little thing pop up and   then   you 're wondering okay how do i get rid   of this little bar so to get rid of it

row=  10250

prediction=  No

F977vuuxAGA191
  you just put your mouse   back up here 

kw_udjD2xwo2
  Animations tab .   Next click the drop down arrow to see all the available effect .   There are four different category : Entrance which will happen when the object   first appears ...   Emphasis which happens while the object is on the slide ...   Exit which will cause the object to disappear ...

row=  10434

prediction=  Visual Aids

kw_udjD2xwo3
  And Motion Paths which will move the object along a path .   I 'm going to choose the one called Fly In which is an Entrance effect .   For some effect you 'll have different Effect Options that you can choose from .   As you can see this one let you change the direction .   Let 's say I wanted to add second animation to the text .   If we try to select one from the main menu it 's actually going to replace the current

row=  10440

prediction=  Visual Aids

kw_udjD2xwo4
  effect .   Instead we 'll click the command that say Add Animation ... and we can apply additional   effect to the same object .   You can always tell wh

KeyboardInterrupt: 

In [142]:
import pandas as pd
df3=pd.read_csv(r'C:\Users\Main\OneDrive - University of Leeds\CharacterisationWorkWithBert_UNI\BERT-binary Topics Training\BERTBinary-Delivery\PresVideosTo6sentencesusingFullStopasDelimiter.csv', encoding='cp1252')
classes = ['VisualAid','']
predictor = ktrain.get_predictor(learner.model, preproc=t_mod)

segmentId=df3['SegmentId']
segList=list(segmentId)

startTime=df3['StartTime']
strList=list(startTime)

endTime=df3['EndTime']
endList=list(endTime)

transcript=df3['Transcript']
transList=list(transcript)
transList1=[]
for i in transList:
    if i != 'nan':
        transList1.append(i)
for i in transList1:
    print(i)
    print()

Pay practitioner today, I'm going to be

teaching you with the help of my friend,

Dana Blouin, the top seven tip for a

great presentation,

Dana blue and a an entrepreneur

currently living in Bangkok, Thailand,

where he is a co and CEO of a

company called mango lab. Anyways here's

some of his tip. We all have to give

presentation at different point in our

life that might be for school or work or

an organization that you weren't

involved with no matter where We give

the presentation, or to who we want to

make sure that it ha the impact on the

Audience and that it memorable, these

are seven tip that are going to ensure

that you nail the presentation, and leave

a lasting impression on your audience.

Number one know your audience. The first

step in preparing for any presentation

should be to get a better idea of who

your audience. is. Knowing your audience.

nan

will allow you to understand the type of

content they are going to be expecting

with regard to depth and t


critical to advance your career but did you know that research say that most adult will

stop listening to your presentation within the first 10 minute if they are n't convinced

there 's something in it for them ?

The problem is that most people do n't know about the skill they need to hook their audience

give a great presentation and overcome their fear of doing it .

What am I going to do ?

Hi Jim .

How 's it going ?

I 'm freaking out about this big presentation I have to give tomorrow .

Well did you write out your opener and practice it three time ?

No .

No ?

Why not ?

I 'm terrified and I do n't even know where to start .

Trust me I 've been in that situation before and it 's not fun .

So to help you out I 'm going to show you my 5 step formula to deliver a killer presentation

opener every time .

Let 's start off with step number one which is Give a Confident Introduction . ''

One of the biggest mistake people make when they start their presentation is showing nerv

Another great thing that happens is

let 's say I 've practiced it three time

and then I sleep on it .

Oftentimes in the middle of the day

I 'm doing other thing I 'm washing dish

my brain keep working on it

and keep figuring out better way to say something

or a quicker way to get to the point .

So in that downtime I believe that our brain

are still working on it

and we benefit from that downtime a well .

The other great thing about breaking up

your practice session is it help me

with my composure in the moment .

Because it feel to me like muscle memory with an athlete

that I 've done this before .

I 've been doing this presentation for day .

So it really help me stay composed and in the moment .

So spread out those practice session three time a day

over three day .

That usually is about what you need .

The number three tip is to focus

on only one or two improvement

each time you practice it through .

So you might just work on your structure and your outline

in 

I work in search engine marketing. I make

sure that the website for the company

go really high up in thing like

Google, because it s really important for

the company to be seen by lot of people,

because then people will buy stuff it s

really important and so I do thing like

making sure there are lot of keywords

on the page and making sure there s no

duplication between page, and there are

lot of thing that you, can do and it s

really important and yeah that s that s

it Okay Laura thanks very much for that

that wa fantastic. So what I m gon na do

is give you a bit of feedback now and

then I m going to ask in a moment just

to do it again with some improvement.

First thing to say is: I think the

content wa fantastic. If you saw that

written down it would sound tremendous.

You said all the right thing but I

think made me there s some way in the

delivery. We could get that across a

little bit more. You just look a little

bit kind of uncomfortable a If you

do nt real

When we stand and present we want to come across a confident and composed .

And one of the great way to do that is by working on our body language . Let 's

look at three way to improve your nonverbal body language in presentation .

Coming up .

Hello again friend . If you never seen one of my video I 'm Alex Lyon .

nan

And this channel Communication Coach is here to help you increase

your impact so you can lead your team to higher level of excellence . And I

believe that presentation skill are a really important part of leadership .

You 're going to be standing and presenting quite frequently if you 're in

any kind of leadership position . So we want to get just a little bit better at

this . Let 's look at three way you can improve your nonverbal body language so

that people can hear your message in a much more confident and composed way .

And these tip by the way go together . So each of the three tip have a couple of

piece a you 'll see . So the first tip is eye contact 


right ? So we 've seen a zillion example like this of people presenting journal club or seminar

you see a slide like that we a audience member are visually overwhelmed we 're lost we do n't know what to look at

we ca n't read this stuff it 's too much to read we 're distracted . The minute a slide like this go up the speaker ha lost the audience completely .

nan

So it take a lot of work do n't get me wrong it take time to use PowerPoint or Keynote effectively in a seminar because you have to think carefully

about what you need to present what you NEED to present not what you want to present not what you 'd love to present but what you need to present

and to present it using clear simple graphic and clear simple text . So in fact let 's go through an exercise .

nan

Let 's take that previous slide from this lovely paper from JCB which I actually presented for a journal club many year ago .

Let 's take that previous slide which is figure 2 from that paper and let 's see how we c

In [143]:
i=0
segTranscript=[]
allSegmentsTrans=[]
startime=strList[0]
endTime=endList[0]
segTrigger=segList[i]
transcriptAsString=''
while i < len(segList)-2:
    #print(segList[i])
    #print()
    if str(segList[i+1])==str('nan') :
        #print(segList[i],'  ==  ',segList[i],'  OR ', 'nan')
        #print()
        segTranscript.append(transList1[i])
        #segTranscript.append(transList1[i+1])
        print( transList1[i])
        #print( transList1[i+1])
        print()
        
        i+=1
    else:
        print(segList[i],'  !=  ',segList[i+1])
        #print()
        #print('start time= ',strList[i+1],'    ','end time= ',endList[i+1])

        segTranscript.append(transList1[i])
        listToString=' '.join([str(item) for item in segTranscript ])
        allSegmentsTrans.append([segTrigger,startime,endTime,segTranscript,listToString])
        print(listToString)
        print()
        segTranscript=[]
        transcriptAsString=''

        startime=strList[i+1]
        endTime=endList[i+1]
        segTrigger=segList[i+1]

        i+=1

Pay practitioner today, I'm going to be

teaching you with the help of my friend,

Dana Blouin, the top seven tip for a

great presentation,

Dana blue and a an entrepreneur

currently living in Bangkok, Thailand,

where he is a co and CEO of a

nan   !=   MnIPpUiTcRc2
Pay practitioner today, I'm going to be teaching you with the help of my friend, Dana Blouin, the top seven tip for a great presentation, Dana blue and a an entrepreneur currently living in Bangkok, Thailand, where he is a co and CEO of a company called mango lab. Anyways here's

MnIPpUiTcRc2   !=   MnIPpUiTcRc3
some of his tip. We all have to give

presentation at different point in our

life that might be for school or work or

an organization that you weren't

involved with no matter where We give

the presentation, or to who we want to

make sure that it ha the impact on the

Audience and that it memorable, these

are seven tip that are going to ensure

that you nail the presentation, and leave

nan   !=   MnIPpUiTcR


presentation? Let s look at that Well, a

lot of people? actually have a nightmare

when it come to giving a presentation

in a room full of people? it is not an

nan   !=   ADJAcyTq1us9
define what is a presentation what Do you exactly mean by the word presentation? Let s look at that Well, a lot of people? actually have a nightmare when it come to giving a presentation in a room full of people? it is not an easy task, I must say when I started.

ADJAcyTq1us9   !=   ADJAcyTq1us10
training a couple of year back. I

actually felt another breakdown because

of the fact that I had to give a

presentation in front of a room of

people? I felt dizzy a Well, a nervous

nan   !=   ADJAcyTq1us11
actually felt another breakdown because of the fact that I had to give a presentation in front of a room of people? I felt dizzy a Well, a nervous and my hand started to sweat. Well, this,

is a phenomenon which happens with most

of the people They get a nightmare about

giving a presentation you Hav

minute are extremely important to hold on to your audience organize your presentation in a clear, and simple manner: keep it very simple and not used to meet jargon word, create an effective conclusion a important. a

ADJAcyTq1us141   !=   ADJAcyTq1us142
an introduction. a conclusion is also

ADJAcyTq1us142   !=   ADJAcyTq1us143
very important. some spontaneous

conversational and enthusiastic nothing

nan   !=   ADJAcyTq1us144
conversational and enthusiastic nothing work. Well, then having a conversation

with your people? rather, than making It

very slight, grooving presentation use

The method of having a casual and

conversational thing with your audience

nan   !=   ADJAcyTq1us145
with your people? rather, than making It very slight, grooving presentation use The method of having a casual and conversational thing with your audience use visual aid. to aid. the presentation

ADJAcyTq1us145   !=   ADJAcyTq1us146
nan

ADJAcyTq1us146   !=   ADJAcyTq1us147
any kind of visual aid. in te

nan   !=   hMk5s1y486I51
diagnosing the problem shed some light on the idea and how the problem can be solved, this is called the vision. Then

hMk5s1y486I51   !=   hMk5s1y486I52
come. the important part present solid

hMk5s1y486I52   !=   hMk5s1y486I53
option that would solve the issue. Use

test, experiment, research, data, anything

nan   !=   hMk5s1y486I54
test, experiment, research, data, anything you possibly have a proof and a story.

to give backbone to your idea and

finally, you want to close out with your

best option tell the audience the fine

print on What the next step to take are

nan   !=   hMk5s1y486I55
to give backbone to your idea and finally, you want to close out with your best option tell the audience the fine print on What the next step to take are and finish with the hook. The conclusion,

with an added bonus to the solution

check out This by Enrique Salah

after 10 year of research, he s hoping

to turn high into natural reserve,

solving oceanic destruction 

fzIxD1jXn4430   !=   fzIxD1jXn4431
Good speaker grab your attention and don ’ t let go .

fzIxD1jXn4431   !=   fzIxD1jXn4432
You want to hear what they have to say .

fzIxD1jXn4432   !=   fzIxD1jXn4433
You feel interested and energised by listening to them .

fzIxD1jXn4433   !=   fzIxD1jXn4434
Bad speaker are the opposite .

fzIxD1jXn4434   !=   fzIxD1jXn4435
Even if you try to make yourself listen you find that your attention drift away .

fzIxD1jXn4435   !=   fzIxD1jXn4436
Your eyelid feel heavy and you have to struggle to stay awake .

So here ’ s a question : what ’ s the difference between good speaker and bad speaker ?

And how can you make sure you speak effectively when you make your presentation in English ?

nan   !=   fzIxD1jXn4437
So here ’ s a question : what ’ s the difference between good speaker and bad speaker ? And how can you make sure you speak effectively when you make your presentation in English ? Here ’ s one way to think about it : bad speaker don ’ t think the

...

nan   !=   Jv18JGOk06o45
failure here, so you want to keep on of it set up and test equipment make sure your laptop your PowerPoint, presentation, work If you re doing something online, you have? recept reception, so get there early, because that light that way, time you give yourself, time If something go. awry to have a backup,

number to the presentation,

this one right here is a study in itself

nan   !=   Jv18JGOk06o46
number to the presentation, this one right here is a study in itself when you become a, if you go. into,

presentation this Is an area, of study

where you can

of time? working with

class to learn this this skill,

the presentation, there are three part

there s the intro there s the

that you re delivering and the So

the intro is coming out with

either a question or a quote

statistic: some hook that get your

nan   !=   Jv18JGOk06o47
presentation this Is an area, of study where you can of time? working with class to learn this this skill, the presentation, th

Now let 's get started with my slide design tip .

TQiln3CjtvM11   !=   TQiln3CjtvM12
Number one visualize your data .

TQiln3CjtvM12   !=   TQiln3CjtvM13
Presenting number and data can be a challenge .

TQiln3CjtvM13   !=   TQiln3CjtvM14
For one it 's probably not the most exciting topic .

And second if you put a lot of data on your slide

the audience is going to be busy reading the slide

nan   !=   TQiln3CjtvM15
And second if you put a lot of data on your slide the audience is going to be busy reading the slide instead of paying attention to you .

Here 's an example a slide like this

encourages the audience to read and try to make sense

nan   !=   TQiln3CjtvM16
Here 's an example a slide like this encourages the audience to read and try to make sense of the data .

Their attention is going to be on the slide

nan   !=   TQiln3CjtvM17
Their attention is going to be on the slide not on what you 're saying .

TQiln3CjtvM17   !=   TQiln3CjtvM18
Instead you could present it like thi

nan   !=   PgOD1j2DhNg132
And sticker are element that are pretty much used to protect yourself .

So why could this be important ?

Why would you need to protect yourself ?

So let 's imagine you make an analysis

which might be a bit controversial

you know that their resides

nan   !=   PgOD1j2DhNg133
So why could this be important ? Why would you need to protect yourself ? So let 's imagine you make an analysis which might be a bit controversial you know that their resides will not please everybody .

And what you can do is

to include such a for discussion sticker

then if you walk into a meeting

then you realize that your analysis spark

some discussion and then yet you can say

nan   !=   PgOD1j2DhNg134
And what you can do is to include such a for discussion sticker then if you walk into a meeting then you realize that your analysis spark some discussion and then yet you can say well  Yes of course this is not the final result . ''

PgOD1j2DhNg134   !=   PgOD1j2DhNg135
 This is

it 's got some result in a gel and it 's got some image of cell . How might I do that ? Well

Hp7Id3Yb9XQ178   !=   Hp7Id3Yb9XQ179
here 's the first figure here 's the first slide in presenting this figure . Notice that there 's a sentence at the top and then I 've taken the data

Hp7Id3Yb9XQ179   !=   Hp7Id3Yb9XQ180
from the figure and I 've added some stuff over here . I 've added two label that help the audience

Hp7Id3Yb9XQ180   !=   Hp7Id3Yb9XQ181
understand immediately that this is a PCR product and this is actually a Western blot .

Hp7Id3Yb9XQ181   !=   Hp7Id3Yb9XQ182
So I 've added some stuff to be helpful to the audience but I 've simplified their focus so there 's a good match between showing this and having the text .

Hp7Id3Yb9XQ182   !=   Hp7Id3Yb9XQ183
And what I would be saying if I were actually presenting a journal club . And then using a simple animation

Hp7Id3Yb9XQ183   !=   Hp7Id3Yb9XQ184
I would then unveil the rest of this panel . And I 've added something for t

RHX-xnP_G5s25   !=   RHX-xnP_G5s26
hardware selling an experience. If

you offer number and statistic make

them meaningful, we have sold four

nan   !=   RHX-xnP_G5s27
you offer number and statistic make them meaningful, we have sold four million iPhones to date. divided

RHX-xnP_G5s27   !=   RHX-xnP_G5s28
four million by two hundred day.

20000 iPhones every day on average

number, mean much unless

placed in context manager connect the

dot for your listener Recently I

worked with a company, that launched a 12

gigabyte memory card 12 gigabyte that

number mean much to most people

So we put into context we said

nan   !=   RHX-xnP_G5s29
20000 iPhones every day on average number, mean much unless placed in context manager connect the dot for your listener Recently I worked with a company, that launched a 12 gigabyte memory card 12 gigabyte that number mean much to most people So we put into context we said enough memory to listen. to your music,

while traveling to the moon and bac

In [140]:
for i in allSegmentsTrans:
    print(i)
    print()

['MnIPpUiTcRc1', 0.01, 0.14, ["Pay practitioner today, I'm going to be", 'teaching you with the help of my friend,', 'Dana Blouin, the top seven tip for a', 'great presentation,', 'Dana blue and a an entrepreneur', 'currently living in Bangkok, Thailand,', 'where he is a co and CEO of a', "company called mango lab. Anyways here's"], "Pay practitioner today, I'm going to be teaching you with the help of my friend, Dana Blouin, the top seven tip for a great presentation, Dana blue and a an entrepreneur currently living in Bangkok, Thailand, where he is a co and CEO of a company called mango lab. Anyways here's"]

['MnIPpUiTcRc2', 0.14, 0.17, ['some of his tip. We all have to give'], 'some of his tip. We all have to give']

['MnIPpUiTcRc3', 0.17, 0.34, ['presentation at different point in our', 'life that might be for school or work or', "an organization that you weren't", 'involved with no matter where We give', 'the presentation, or to who we want to', 'make sure that it ha the impact o

['Iwpi1Lm6dFo182', 17.43, 17.47, ['Your perceptive limit', 'is here .'], 'Your perceptive limit is here .']

['Iwpi1Lm6dFo183', 17.5, 18.06, ['Now what amazes me', 'is that whichever country I go to whichever company I see', 'it seems like they build PowerPoints', 'in the hope that all their fellow colleague are autistic or savant', 'which obviously is not the case .'], 'Now what amazes me is that whichever country I go to whichever company I see it seems like they build PowerPoints in the hope that all their fellow colleague are autistic or savant which obviously is not the case .']

['Iwpi1Lm6dFo184', 18.11, 18.11, ["So but then you go like this 'But David my god ."], "So but then you go like this 'But David my god ."]

['Iwpi1Lm6dFo185', 18.16, 18.16, ["This mean that I have to have more slide . '"], "This mean that I have to have more slide . '"]

['Iwpi1Lm6dFo186', 18.16, 18.23, ["'Yes that is entirely correct ."], "'Yes that is entirely correct ."]

['Iwpi1Lm6dFo187', 18.26, 18.2

In [144]:
#### 
# Write the annotation result to Excel File

import xlrd
import xlsxwriter
workbook = xlsxwriter.Workbook('PresentationCorpusAnnotatedUsingBertBaseUncaseWithFullStop-BinaryVisualAid.xlsx')
worksheet = workbook.add_worksheet('Sheet1')
worksheet.write('A1', 'SegmentId')
worksheet.write('B1', 'StartTime')
worksheet.write('C1', 'EndTime')
worksheet.write('D1', 'Transcript')
worksheet.write('E1', 'Topic')
row=1
col=0
transRow=0

for i in allSegmentsTrans:
    print(i[0])
    print(i[4])
    print()
    print('row= ',row)
    print()
    mainRow=row
    worksheet.write(row,col,str(i[0]))
    worksheet.write(row,col+1,str(i[1]))
    worksheet.write(row,col+2,str(i[2]))
    transRow=row
    for j in i[3]:
        worksheet.write(row,col+3,str(j))
        row+=1
    print('prediction= ',predictor.predict(i[4]))
    print()
    worksheet.write(mainRow,col+4,predictor.predict(str(i[4])))
        
        

    
workbook.close()        


MnIPpUiTcRc1
Pay practitioner today, I'm going to be teaching you with the help of my friend, Dana Blouin, the top seven tip for a great presentation, Dana blue and a an entrepreneur currently living in Bangkok, Thailand, where he is a co and CEO of a company called mango lab. Anyways here's

row=  1

prediction=  No

MnIPpUiTcRc2
some of his tip. We all have to give

row=  9

prediction=  No

MnIPpUiTcRc3
presentation at different point in our life that might be for school or work or an organization that you weren't involved with no matter where We give the presentation, or to who we want to make sure that it ha the impact on the Audience and that it memorable, these are seven tip that are going to ensure that you nail the presentation, and leave a lasting impression on your audience.

row=  10

prediction=  No

MnIPpUiTcRc4
Number one know your audience. The first

row=  20

prediction=  No

MnIPpUiTcRc5
step in preparing for any presentation should be to get a better idea of who you

prediction=  No

MnIPpUiTcRc39
figure and no one want to listen to someone with no confidence. So there a

row=  181

prediction=  Visual Aids

MnIPpUiTcRc40
fine balance, you need a strike and here, how the most important thing you can do to come across a more relatable is to be authentic, be yourself. Another

row=  183

prediction=  No

MnIPpUiTcRc41
great way to accomplish this is to work on coming across a relaxed which can be difficult. If you not used to

row=  187

prediction=  No

MnIPpUiTcRc42
presenting, but This go a long way to helping people, see you a relatable the final way you can be a more relatable is to be enthusiastic about your presentation your enthusiasm will transfer to your audience. and now that

row=  190

prediction=  No

MnIPpUiTcRc43
you have enthusiasm in common you will begin to see is more relatable If you get all three of these technique mastered, you will be we'll On your way to making it to your audience. relate to, you

row=  196

prediction=  No



prediction=  No

yoD8RMq2OkU38
After your pitch the audience know everything they need to know but they don ’ t fund you .

row=  322

prediction=  No

yoD8RMq2OkU39
Did you succeed ? No .

row=  324

prediction=  No

yoD8RMq2OkU40
Now imagine that after your pitch your audience doe give you the fund because they feel confident and trusting and they believe that your project will be successful and that it is a good investment .

row=  326

prediction=  No

yoD8RMq2OkU41
All of that is not information it ’ s transformation .

row=  330

prediction=  No

yoD8RMq2OkU42
So it ’ s easy for me to say “ Don ’ t inform transform ! ” but how ? Well every magician need a magic wand and here is yours .

row=  331

prediction=  No

yoD8RMq2OkU43
It ’ s called the  Audience Transformation Roadmap . ''

row=  334

prediction=  No

yoD8RMq2OkU44
This is a really simple but amazingly powerful technique to understand what your transformational objective are and then to brainstorm what you can say show 

prediction=  No

yoD8RMq2OkU90
I need to make them motivated and optimistic .

row=  441

prediction=  No

yoD8RMq2OkU91
Well I can make them optimistic by explaining how easy this is to use but also how powerful it is .

row=  442

prediction=  No

yoD8RMq2OkU92
And to motivate them to try it I ’ m going to need to explain that successful presentation can really make a difference to how well they succeed in life .

row=  444

prediction=  No

yoD8RMq2OkU93
Lastly to make them do these thing I ’ ll need a call to action which focus on what I want them to do afterwards .

row=  447

prediction=  No

yoD8RMq2OkU94
So there we have it ! That ’ s a very accelerated version of the brainstorming but it doesn ’ t need to take long .

row=  449

prediction=  No

yoD8RMq2OkU95
What we have now is just enough relevant idea on how we can transform our audience .

row=  452

prediction=  No

yoD8RMq2OkU96
So what happens next ? Well this is where I ’ m going to take my magic wand out again because

prediction=  No

dEDcc0aCjaA31
What 's your credential statement ? You 'll be amazed at the effect this ha on your audience .

row=  554

prediction=  No

dEDcc0aCjaA32
Step 3 is to Deliver Your Hook . ''

row=  556

prediction=  No

dEDcc0aCjaA33
My hook for this video presentation might look something like this I 'm going to show you how to captivate your audience within the first 5 minute of your presentation . ''

row=  557

prediction=  No

dEDcc0aCjaA34
When you do this you have to get your audience to feel '' something .

row=  559

prediction=  No

dEDcc0aCjaA35
How do you get them to feel ? You have 3 choice .

row=  560

prediction=  No

dEDcc0aCjaA36
You can get them to feel more happy more successful or more free .

row=  562

prediction=  No

dEDcc0aCjaA37
Look at my hook .

row=  563

prediction=  No

dEDcc0aCjaA38
I said I 'm going to show you how to captivate your audience within the first 5 minute of your presentation . ''

row=  564

prediction=  No

dEDcc0aCjaA39
Whe

...

prediction=  No

1VCaJ4dSHak4
So I am going to walk you through the four gesture that you can use in your presentation and so you can become more powerful and effective public speaker .

row=  6057

prediction=  No

1VCaJ4dSHak5
Gesture number one are descriptive Gestures so these are gesture that we are using to describe something or situation .We might draw comparison between something thats really big and something thats really small or we might use it to contrast certain item or to depict the size .

row=  6059

prediction=  No

1VCaJ4dSHak6
A great example that I am taking from toy master is if you are using a metaphor something is like a tiny little bird and you are holding like cup stand stating the metaphor of the bird and also implying size being small .

row=  6063

prediction=  No

1VCaJ4dSHak7
You can also use descriptive gesture to say shape say it wa the box this big back these and you showing square shape of the box using your gesture .

row=  6066

prediction=  No

1VCa

prediction=  No

h6sm47j-Am418
Now having said that I 'm gon na sound like I 'm contradicting myself but I am not .

row=  6160

prediction=  No

h6sm47j-Am419
There 's a lot of way to add humor to your attention grabber without the big risk .

row=  6162

prediction=  No

h6sm47j-Am420
So let 's look at three easy way to add some lighthearted humor and still grab your audience 's attention .

row=  6164

prediction=  No

h6sm47j-Am421
The first way is to deliberately quote someone else that 's funny .

row=  6167

prediction=  No

h6sm47j-Am422
Now by quoting them directly by saying a Jerry Seinfeld once said or a George Burns once said then you may even have the piece of paper in your hand and read the quotation .

row=  6169

prediction=  No

h6sm47j-Am423
What you 're doing there is you 're drawing people 's attention to what that other person said and it take the attention off of you a the joke teller .

row=  6173

prediction=  No

h6sm47j-Am424
So you know they have a funny line

prediction=  No

i68a6M5FFBc&t17
Jim us a simple pad of paper or sicky note . Staying low tech at this stage help him think

row=  6290

prediction=  No

i68a6M5FFBc&t18
more creatively and stay outside the box . He then considers what tool will help him

row=  6291

prediction=  No

i68a6M5FFBc&t19
best tell his story . Jim sometimes opts to use a whiteboard flip chart handout or

row=  6292

prediction=  Visual Aids

i68a6M5FFBc&t20
even no prop at all . When it make sense for him to use PowerPoint he try to remember

row=  6293

prediction=  Visual Aids

i68a6M5FFBc&t21
the adage that sometimes le is more . '' He doe n't dumb down his presentation

row=  6294

prediction=  No

i68a6M5FFBc&t22
but he doe try to limit each slide to one key idea . Or depending on the content he

row=  6295

prediction=  Visual Aids

i68a6M5FFBc&t23
sometimes build an idea incrementally so it 's easy to follow . He look for visual

row=  6296

prediction=  No

i68a6M5FFBc&t24
way to tell his story with 

Yl_FJAOcFgQ41
nan

row=  6435

prediction=  No

Yl_FJAOcFgQ42
quote word of wisdom So I going to be totally predictable and do the same.

row=  6436

prediction=  No

Yl_FJAOcFgQ43
An ancient philosopher once said a man, who chase two rabbit catch. Neither

row=  6438

prediction=  No

Yl_FJAOcFgQ44
in our research been chasing too many rabbit for far too long. it, time, to

row=  6440

prediction=  No

Yl_FJAOcFgQ45
stop. to prioritize. If one thing,

row=  6442

prediction=  No

Yl_FJAOcFgQ46
nan

row=  6443

prediction=  No

Yl_FJAOcFgQ47
we now. need to do in a word it This

row=  6444

prediction=  No

Yl_FJAOcFgQ48
focus. Thank you very much

row=  6445

prediction=  No

Yl_FJAOcFgQ49
at the preparation stage, a lot of presenter like to create their clothes.

row=  6446

prediction=  No

Yl_FJAOcFgQ50
first, so They know. where going

row=  6448

prediction=  No

Yl_FJAOcFgQ51
and then work backwards finishing up with an attention opening. But

row=  6449

prediction=  No

Yl_FJA

prediction=  No

RHX-xnP_G5s52
wish you, a dazzling presentation for more information, go to be Netcom.

row=  6598

prediction=  No

7MWaeOHDBOg1
Presentation or talking to your bos in the elevator, there are five secret to being a confident speaker. First,

row=  6600

prediction=  No

7MWaeOHDBOg2
your stance. Second, your sound third

row=  6603

prediction=  No

7MWaeOHDBOg3
smile, fourth silence and fit your site.

row=  6604

prediction=  No

7MWaeOHDBOg4
First, your stance. when you

row=  6605

prediction=  No

7MWaeOHDBOg5
you need to have a nice firm stance. your

row=  6606

prediction=  No

7MWaeOHDBOg6
foot should be about hip apart, not too wide and not too close. We want to

row=  6607

prediction=  No

7MWaeOHDBOg7
have our foot firmly planted on the ground, no crossing of the leg, no swaying back and forth no dancing backwards and forward no pacing side and by all mean no popping of the hip Once we have that firm, stable stance, we need to then stand up nice and tall 